In [213]:
%matplotlib inline
import matplotlib.pyplot as plt
import librosa.display
import tensorflow as tf
import tensorflow_hub as hub
from IPython.display import display, Audio
import numpy as np
from wavegan import sample_context_embeddings

In [214]:
def generate(cond_texts, num_samples_per_cond, inference_graph_path, model_ckpt_path, embed_model='elmo'):
    cond_texts = cond_texts.tolist()
    tmp_list = []
    for cond_text in cond_texts:
        tmp_list += [cond_text] * num_samples_per_cond
    cond_texts = tmp_list
        
    _z = (np.random.randn(len(cond_texts), 128))
    
    with tf.Session() as sess:
        #print([n.name for n in tf.get_default_graph().as_graph_def().node])
        if embed_model == 'elmo':
            embed = hub.Module("https://tfhub.dev/google/elmo/2", trainable=False, name='embed')
        elif embed_model == 'nnlm':
            embed = hub.Module("https://tfhub.dev/google/nnlm-en-dim128-with-normalization/1", trainable=False, name='embed')
            
        embeddings = embed(cond_texts)

        sess.run(tf.global_variables_initializer())
        sess.run(tf.tables_initializer())
        _fake_conditionals = sess.run(embeddings)

    # Load the graph
    graph = tf.Graph()
    with graph.as_default():
        saver = tf.train.import_meta_graph(inference_graph_path)
        with tf.Session() as sess:
            saver.restore(sess, model_ckpt_path)

            # Synthesize G(z)
            z = graph.get_tensor_by_name('z:0')
            c = graph.get_tensor_by_name('c:0')
            G_z = graph.get_tensor_by_name('G_z:0')
            _G_z = sess.run(G_z, {z: _z, c: _fake_conditionals})
            return zip(_G_z, cond_texts)

In [215]:
def load_cond_texts(file_path):
    cond_texts = np.genfromtxt(file_path, delimiter=',', dtype=None, encoding='utf8')
    return cond_texts

In [216]:
def gen_random_samples(cond_dataset, num_cond_samples, num_samples_per_cond, inference_graph_path, model_ckpt_path):
    cond_texts = np.random.choice(cond_dataset, num_cond_samples, replace=False)
    audio_set = generate(cond_texts, num_samples_per_cond, inference_graph_path, model_ckpt_path)
    print(label)
    for audio_data in audio_set:
        audio = audio_data[0]
        cond_text = audio_data[1]
        print(cond_text)
        display(Audio(audio.flatten(), rate=16000))

In [217]:
cond_texts_dataset = load_cond_texts('./data/vocab.tsv')

In [212]:
gen_random_samples(cond_texts_dataset, 10, 5, './train_tconv_600k/infer/infer.meta', './train_tconv_600k/model.ckpt-677768')

INFO:tensorflow:Saver not created because there are no variables in the graph to restore
INFO:tensorflow:Restoring parameters from ./train_tconv_600k/model.ckpt-677768
angry close
large whoosh swirl


large whoosh swirl


large whoosh swirl


large whoosh swirl


large whoosh swirl


...

owl bird


owl bird


owl bird


owl bird


owl bird


In [218]:
gen_random_samples(cond_texts_dataset, 10, 5, './train_nn_opt_reset_325k/infer/infer.meta', './train_nn_opt_reset_325k/model.ckpt-325520')

INFO:tensorflow:Saver not created because there are no variables in the graph to restore
INFO:tensorflow:Restoring parameters from ./train_nn_opt_reset_325k/model.ckpt-325520
angry close
magic black spirit


magic black spirit


magic black spirit


magic black spirit


magic black spirit


...

blood


blood


blood


blood


blood
